#Geocoder & Maps

## Importing libraries 

In [13]:
from bs4 import BeautifulSoup
import requests
import html5lib
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium 
print('Libraries imported.')

Libraries imported.


## Read previously saved Dataframe

In [4]:
df = pd.read_csv('neighborhoods.csv', index_col=0)
df.head()

Postcode           Borough      Neighborhood
0      M3A        North York         Parkwoods
1      M4A        North York  Victoria Village
2      M5A  Downtown Toronto      Harbourfront
3      M6A        North York  Lawrence Heights
4      M6A        North York    Lawrence Manor

In [5]:
df.shape

(210, 3)

In [6]:
#import Geospatial data

gdata = pd.read_csv('https://cocl.us/Geospatial_data')
gdata.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [7]:
float(gdata.loc[gdata['Postal Code'] == 'M1C']['Latitude']
)

43.7845351

#Add Geo Data to the main dataframe

In [0]:
lat=[]
lg = []
for index, row in df.iterrows():
  pcode = row.Postcode
  lat.append( float(gdata.loc[gdata['Postal Code'] == pcode]['Latitude']))
  lg.append(float(gdata.loc[gdata['Postal Code'] == pcode]['Longitude']) )

df["Latitude"] = np.asarray(lat)
df["Longitude"] = np.asarray(lg)

In [9]:
df.head()

Postcode           Borough      Neighborhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df['Borough'].unique()),
        df.shape[0]
    )
)

The dataframe has 11 boroughs and 210 neighborhoods.


# Explore Toronto

## Get Coordinates

In [15]:
adress = 'Toronto'
geolocator = Nominatim(user_agent='Toronto_explorer')
location = geolocator.geocode(adress)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinates of Toronto are {}, {}'.format(latitude, longitude))

The geographical coordinates of Toronto are 43.653963, -79.387207


#### Create a map of Toronto with neighborhoods superimposed on top.

In [0]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)
for lat, lng, borough, neighborhood in zip (df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
  label = '{}, {}'.format(neighborhood, borough)
  label = folium.Popup(label, parse_html=True)
  folium.CircleMarker([lat,lng], radius=5, popup=label, color = 'blue', fill = True, fill_color='#3186cc', fill_opacity = 0.7, parse_html = False  
  ).add_to(map_toronto)
map_toronto

**Define Foursquare Credentials and Version**

In [28]:
CLIENT_ID = '5XSGY3GLOGHUERBFO1NU24OVBXG2ZFEXGY4B2YM4XFMDEL0E' # your Foursquare ID
CLIENT_SECRET = 'WVKFY41MCNVUWNPCWTK2INLLRQV01G01WXEL1KLEI1W0NOHF' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 5XSGY3GLOGHUERBFO1NU24OVBXG2ZFEXGY4B2YM4XFMDEL0E
CLIENT_SECRET:WVKFY41MCNVUWNPCWTK2INLLRQV01G01WXEL1KLEI1W0NOHF


In [29]:
df.head()

Postcode           Borough      Neighborhood   Latitude  Longitude
0      M3A        North York         Parkwoods  43.753259 -79.329656
1      M4A        North York  Victoria Village  43.725882 -79.315572
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636
3      M6A        North York  Lawrence Heights  43.718518 -79.464763
4      M6A        North York    Lawrence Manor  43.718518 -79.464763

In [30]:
df.loc[0,'Neighborhood']

'Parkwoods'

In [31]:
neighborhood_latitude = df.loc[0, 'Latitude'] 
neighborhood_longitude = df.loc[0, 'Longitude'] 

neighborhood_name = df.loc[0, 'Neighborhood'] 

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


###  top 100 venues

In [32]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=5XSGY3GLOGHUERBFO1NU24OVBXG2ZFEXGY4B2YM4XFMDEL0E&client_secret=WVKFY41MCNVUWNPCWTK2INLLRQV01G01WXEL1KLEI1W0NOHF&v=20180605&ll=43.7532586,-79.3296565&radius=500&limit=100'

In [0]:
results = requests.get(url).json()
results

In [0]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [36]:

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0             Brookbanks Park               Park  43.751976 -79.332140
1               Variety Store  Food & Drink Shop  43.751974 -79.333114
2  TTC stop - 44 Valley Woods           Bus Stop  43.755402 -79.333741

In [37]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

3 venues were returned by Foursquare.


**Explore Neighborhoods in Parkwoods**

In [0]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [94]:
parkwoods_venues = getNearbyVenues(names=df['Neighborhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )


Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Queen's Park
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toronto 

In [95]:
print(parkwoods_venues.shape)
parkwoods_venues.head()

(4347, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                        Venue  Venue Latitude  Venue Longitude  \
0             Brookbanks Park       43.751976       -79.332140   
1               Variety Store       43.751974       -79.333114   
2  TTC stop - 44 Valley Woods       43.755402       -79.333741   
3      Victoria Village Arena       43.723481       -79.315635   
4                 Tim Hortons       43.725517       -79.313103   

      Venue Category  
0               Park  
1  Food & Drink Shop  
2           Bus Stop  
3       Hockey Arena  
4        Coffee Shop

In [97]:
parkwoods_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Agincourt                                                              4   
Agincourt North                                                        4   
Albion Gardens                                                        10   
Alderwood                                                             10   
Bathurst Manor                                                        19   
Bathurst Quay                                                         16   
Bayview Village                                                        4   
Beaumond Heights                                                      10   
Bedford Park                                                          23   
Berczy Park                                                           55   
Birch Cliff                                                            5   
Bloordale Gardens                                                      8   
Brockton                                                              22   
Business Reply Mail Processing Centre 969 Eastern                     18   
CFB Toronto                                                            3   
CN Tower                                                              16   
Cabbagetown                                                           45   
Caledonia-Fairbanks                                                    5   
Canada Post Gateway Processing Centre                                 10   
Cedarbrae                                                              8   
Central Bay Street                                                    86   
Chinatown                                                             90   
Christie                                                              17   
Church and Wellesley                                                  82   
Clairlea                                                              10   
Clarks Corners                                                        13   
Cliffcrest                                                             2   
Cliffside                                                              2   
Cliffside West                                                         5   
Commerce Court                                                       100   
Davisville                                                            33   
Davisville North                                                      10   
Deer Park                                                             15   
Del Ray                                                                4   
Design Exchange                                                      100   
Don Mills North                                                        5   
Don Mills South                                                       22   
Dorset Park                                                            6   
Dovercourt Village                                                    18   
Downsview                                                              4   
Downsview Central                                                      3   
Downsview East                                                         3   
Downsview North                                                       19   
Downsview Northwest                                                    4   
Downsview West                                                         6   
Dufferin                                                              18   
East Birchmount Park                                                   5   
East Toronto                                                           4   
Emery                                                                  2   
Eringate                                                               8   
Exhibition Place       

In [98]:
print('There are {} uniques categories.'.format(len(parkwoods_venues['Venue Category'].unique())))

There are 277 uniques categories.


In [99]:
# one hot encoding
parkwood_onehot = pd.get_dummies(parkwoods_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
parkwood_onehot['Neighborhood'] = parkwoods_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [parkwood_onehot.columns[-1]] + list(parkwood_onehot.columns[:-1])
parkwood_onehot = parkwood_onehot[fixed_columns]

parkwood_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Workshop  \
0                    0                 0                   0              0   
1                    0                 0                   0              0   
2                    0                 0                   0              0   
3                    0                 0                   0              0   
4                    0                 0                   0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0       0              0          0         0                     0   
1       0              0          0         0                     0   
2       0              0          0         0                     0   
3       0              0          0         0                     0   
4       0              0          0         0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Building  \
0               0        0            0                0         0   
1               0        0            0                0         0   
2               0        0            0                0         0   
3               0        0            0                0         0   
4               0        0            0                0         0   

   Burger Joint  Burrito Place  Bus Line  Bus Station  Bus

In [100]:
parkwood_onehot.shape

(4347, 277)

In [101]:
parkwoods_grouped = parkwood_onehot.groupby('Neighborhood').mean().reset_index()
parkwoods_grouped

Neighborhood  Yoga Studio  \
0                                             Adelaide     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                       Albion Gardens     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                        Bathurst Quay     0.000000   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                   Bloordale Gardens     0.000000   
13                                            Brockton     0.000000   
14   Business Reply Mail Processing Centre 969 Eastern     0.055556   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.000000   
17                                         Cabbagetown     0.000000   
18                                 Caledonia-Fairbanks     0.000000   
19               Canada Post Gateway Processing Centre     0.000000   
20                                           Cedarbrae     0.000000   
21                                  Central Bay Street     0.011628   
22                                           Chinatown     0.000000   
23                                            Christie     0.000000   
24                                Church and Wellesley     0.012195   
25                                            Clairlea     0.000000   
26                                      Clarks Corners     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                      Cliffside West     0.000000   
30                                      Commerce Court     0.000000   
31                                          Davisville     0.000000   
32                                    Davisville North     0.000000   
33                                           Deer Park     0.000000   
34                                             Del Ray     0.000000   
35                                     Design Exchange     0.000000   
36                                     Don Mills North     0.000000   
37                                     Don Mills South     0.000000   
38                                         Dorset Park     0.000000   
39                                  Dovercourt Village     0.000000   
40                                           Downsview     0.000000   
41                                   Downsview Central     0.000000   
42                                      Downsview East     0.000000   
43                                     Downsview North     0.000000   
44                                 Downsview Northwest     0.000000   
45                                      Downsview West     0.000000   
46                                            Dufferin     0.000000   
47                                East Birchmount Park     0.000000   
48                                        East Toronto     0.000000   
49                                               Emery     0.000000   
50                                            Eringate     0.000000   
51                                    Exhibition Place     0.000000   
52                                            Fairview     0.000000   
53                                First Canadian Place     0.000000   
54                                     Flemingdon Park     0.000000   
55                                   Forest Hill North     0.00000

In [102]:
parkwoods_grouped.shape

(199, 277)

In [103]:
num_top_venues = 5

for hood in parkwoods_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = parkwoods_grouped[parkwoods_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
              venue  freq
0       Coffee Shop  0.07
1              Café  0.04
2        Steakhouse  0.04
3               Bar  0.04
4  Sushi Restaurant  0.03


----Agincourt----
                       venue  freq
0                     Lounge  0.25
1             Breakfast Spot  0.25
2               Skating Rink  0.25
3  Latin American Restaurant  0.25
4                Yoga Studio  0.00


----Agincourt North----
         venue  freq
0         Park  0.25
1          Gym  0.25
2   Playground  0.25
3  Coffee Shop  0.25
4  Yoga Studio  0.00


----Albion Gardens----
                 venue  freq
0        Grocery Store   0.2
1       Discount Store   0.1
2           Beer Store   0.1
3       Sandwich Place   0.1
4  Fried Chicken Joint   0.1


----Alderwood----
          venue  freq
0   Pizza Place   0.2
1      Pharmacy   0.1
2  Skating Rink   0.1
3           Gym   0.1
4           Pub   0.1


----Bathurst Manor----
                  venue  freq
0           Coffee Shop  0.11
1        

In [0]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [140]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = parkwoods_grouped['Neighborhood']

for ind in np.arange(parkwoods_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(parkwoods_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0         Adelaide           Coffee Shop                       Café   
1        Agincourt                Lounge  Latin American Restaurant   
2  Agincourt North                   Gym                       Park   
3   Albion Gardens         Grocery Store                Pizza Place   
4        Alderwood           Pizza Place                        Gym   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
0            Steakhouse                   Bar              Thai Restaurant   
1          Skating Rink        Breakfast Spot  Eastern European Restaurant   
2           Coffee Shop            Playground                    Drugstore   
3  Fast Food Restaurant            Beer Store               Sandwich Place   
4              Pharmacy        Sandwich Place                 Dance Studio   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Burger Joint        Clothing Store                 Hotel   
1               Dog Run      Doner Restaurant            Donut Shop   
2                 Diner        Discount Store               Dog Run   
3   Japanese Restaurant        Discount Store   Fried Chicken Joint   
4    Athletics & Sports                   Pub          Skating Rink   

  9th Most Common Venue      10th Most Common Venue  
0      Sushi Restaurant            Asian Restaurant  
1             Drugstore         Dumpling Restaurant  
2      Doner Restaurant                  Donut Shop  
3              Pharmacy  Construction & Landscaping  
4           Coffee Shop          Dim Sum Restaurant

# Cluster Neighborhoods

In [141]:
# set number of clusters
kclusters = 5

parkwoods_grouped_clustering = parkwoods_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(parkwoods_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 4, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [142]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

parkwoods_merged = df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
parkwoods_merged = parkwoods_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
parkwoods_merged
 # check the last columns!

Postcode           Borough  \
0        M3A        North York   
1        M4A        North York   
2        M5A  Downtown Toronto   
3        M6A        North York   
4        M6A        North York   
5        M7A  Downtown Toronto   
6        M9A      Queen's Park   
7        M1B       Scarborough   
8        M1B       Scarborough   
9        M3B        North York   
10       M4B         East York   
11       M4B         East York   
12       M5B  Downtown Toronto   
13       M5B  Downtown Toronto   
14       M6B        North York   
15       M9B         Etobicoke   
16       M9B         Etobicoke   
17       M9B         Etobicoke   
18       M9B         Etobicoke   
19       M9B         Etobicoke   
20       M1C       Scarborough   
21       M1C       Scarborough   
22       M1C       Scarborough   
23       M3C        North York   
24       M3C        North York   
25       M4C         East York   
26       M5C  Downtown Toronto   
27       M6C              York   
28       M9C         Etobicoke   
29       M9C         Etobicoke   
30       M9C         Etobicoke   
31       M9C         Etobicoke   
32       M1E       Scarborough   
33       M1E       Scarborough   
34       M1E       Scarborough   
35       M4E      East Toronto   
36       M5E  Downtown Toronto   
37       M6E              York   
38       M1G       Scarborough   
39       M4G         East York   
40       M5G  Downtown Toronto   
41       M6G  Downtown Toronto   
42       M1H       Scarborough   
43       M2H        North York   
44       M3H        North York   
45       M3H        North York   
46       M3H        North York   
47       M4H         East York   
48       M5H  Downtown Toronto   
49       M5H  Downtown Toronto   
50       M5H  Downtown Toronto   
51       M6H      West Toronto   
52       M6H      West Toronto   
53       M1J       Scarborough   
54       M2J        North York   
55       M2J        North York   
56       M2J        North York   
57       M3J        North York   
58       M3J        North York   
59       M4J         East York   
60       M5J  Downtown Toronto   
61       M5J  Downtown Toronto   
62       M5J  Downtown Toronto   
63       M6J      West Toronto   
64       M6J      West Toronto   
65       M1K       Scarborough   
66       M1K       Scarborough   
67       M1K       Scarborough   
68       M2K        North York   
69       M3K        North York   
70       M3K        North York   
71       M4K      East Toronto   
72       M4K      East Toronto   
73       M5K  Downtown Toronto   
74       M5K  Downtown Toronto   
75       M6K      West Toronto   
76       M6K      West Toronto   
77       M6K      West Toronto   
78       M1L       Scarborough   
79       M1L       Scarborough   
80       M1L       Scarborough   
81       M2L        North York   
82       M2L        North York   
83       M3L        North York   
84       M4L      East Toronto   
85       M4L      East Toronto   
86       M5L  Downtown Toronto   
87       M5L  Downtown Toronto   
88       M6L        North York   
89       M6L        North York   
90       M6L        North York   
91       M9L        North York   
92       M1M       Scarborough   
93       M1M       Scarborough   
94       M1M       Scarborough   
95       M2M        North York   
96       M2M        North York   
97       M3M        North York   
98       M4M      East Toronto   
99       M5M        North York   
100      M5M        North York   
101      M6M              York   
102      M6M              York   
103      M6M              York   
104      M6M              York   
105      M9M        North York   
106      M9M        North York   
107      M1N       Scarborough   
108      M1N       Scarborough   
109      M2N        North York   
110      M3N        North York   
111      M4N   Central Toronto   
112      M5N   Central Toronto   
113      M6N              York   
114      M6N              York   
115      M9N              York   
116      M1P       Scarbor

In [118]:
parkwoods_merged.head()

Postcode           Borough      Neighborhood   Latitude  Longitude  \
0      M3A        North York         Parkwoods  43.753259 -79.329656   
1      M4A        North York  Victoria Village  43.725882 -79.315572   
2      M5A  Downtown Toronto      Harbourfront  43.654260 -79.360636   
3      M6A        North York  Lawrence Heights  43.718518 -79.464763   
4      M6A        North York    Lawrence Manor  43.718518 -79.464763   

   Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
0             1.0                  Park                Bus Stop   
1             0.0          Hockey Arena       French Restaurant   
2             0.0           Coffee Shop                  Bakery   
3             0.0        Clothing Store  Furniture / Home Store   
4             0.0        Clothing Store  Furniture / Home Store   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0     Food & Drink Shop              Drugstore        Discount Store   
1           Coffee Shop  Portuguese Restaurant   Dumpling Restaurant   
2                  Park                    Pub        Breakfast Spot   
3           Coffee Shop     Miscellaneous Shop              Boutique   
4           Coffee Shop     Miscellaneous Shop              Boutique   

  6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
0               Dog Run      Doner Restaurant             Donut Shop   
1        Discount Store               Dog Run       Doner Restaurant   
2                  Café            Restaurant     Mexican Restaurant   
3          Carpet Store         Women's Store  Vietnamese Restaurant   
4          Carpet Store         Women's Store  Vietnamese Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0   Dumpling Restaurant     Dim Sum Restaurant  
1            Donut Shop              Drugstore  
2        Farmers Market                Brewery  
3     Accessories Store    Empanada Restaurant  
4     Accessories Store    Empanada Restaurant

In [143]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(parkwoods_merged['Latitude'], parkwoods_merged['Longitude'], parkwoods_merged['Neighborhood'], kmeans.labels_):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Cluster 1

In [145]:
parkwoods_merged.loc[parkwoods_merged['Cluster Labels'] == 0, parkwoods_merged.columns[[1] + list(range(5, parkwoods_merged.shape[1]))]]

Borough  Cluster Labels     1st Most Common Venue  \
1          North York             0.0              Hockey Arena   
2    Downtown Toronto             0.0               Coffee Shop   
3          North York             0.0            Clothing Store   
4          North York             0.0            Clothing Store   
5    Downtown Toronto             0.0               Coffee Shop   
6        Queen's Park             0.0               Coffee Shop   
7         Scarborough             0.0      Fast Food Restaurant   
8         Scarborough             0.0      Fast Food Restaurant   
9          North York             0.0                      Café   
10          East York             0.0      Fast Food Restaurant   
11          East York             0.0      Fast Food Restaurant   
12   Downtown Toronto             0.0               Coffee Shop   
13   Downtown Toronto             0.0               Coffee Shop   
14         North York             0.0                      Park   
20        Scarborough             0.0             Moving Target   
21        Scarborough             0.0             Moving Target   
22        Scarborough             0.0             Moving Target   
23         North York             0.0                       Gym   
24         North York             0.0                       Gym   
25          East York             0.0              Skating Rink   
26   Downtown Toronto             0.0               Coffee Shop   
27               York             0.0                     Trail   
28          Etobicoke             0.0         Convenience Store   
29          Etobicoke             0.0         Convenience Store   
30          Etobicoke             0.0         Convenience Store   
31          Etobicoke             0.0         Convenience Store   
32        Scarborough             0.0       Rental Car Location   
33        Scarborough             0.0       Rental Car Location   
34        Scarborough             0.0       Rental Car Location   
35       East Toronto             0.0      Other Great Outdoors   
36   Downtown Toronto             0.0               Coffee Shop   
38        Scarborough             0.0               Coffee Shop   
39          East York             0.0               Coffee Shop   
40   Downtown Toronto             0.0               Coffee Shop   
41   Downtown Toronto             0.0             Grocery Store   
42        Scarborough             0.0          Hakka Restaurant   
43         North York             0.0  Mediterranean Restaurant   
44         North York             0.0               Coffee Shop   
45         North York             0.0               Coffee Shop   
46         North York             0.0               Coffee Shop   
47          East York             0.0         Indian Restaurant   
48   Downtown Toronto             0.0               Coffee Shop   
49   Downtown Toronto             0.0               Coffee Shop   
50   Downtown Toronto             0.0               Coffee Shop   
51       West Toronto             0.0                  Pharmacy   
52       West Toronto             0.0                  Pharmacy   
54         North York             0.0            Clothing Store   
55         North York             0.0            Clothing Store   
56         North York             0.0            Clothing Store   
57         North York             0.0        Falafel Restaurant   
58         North York             0.0        Falafel Restaurant   
60   Downtown Toronto             0.0               Coffee Shop   
61   Downtown Toronto             0.0               Coffee Shop   
62   Downtown Toronto             0.0               Coffee Shop   
63       West Toronto             0.0                       Bar   
64       West Toronto             0.0                       Bar   
65        Scarborough             0.0            Discount Store   
66        Scarborough             0.0            Discount Store   
67        Scarborough             0.0            Discount Sto

Cluster 2

In [148]:
parkwoods_merged.loc[parkwoods_merged['Cluster Labels'] == 1, parkwoods_merged.columns[[1] + list(range(5, parkwoods_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
0          North York             1.0                  Park   
37               York             1.0                  Park   
59          East York             1.0                  Park   
69         North York             1.0                  Park   
70         North York             1.0                  Park   
115              York             1.0                  Park   
119        North York             1.0                  Park   
182  Downtown Toronto             1.0                  Park   
192         Etobicoke             1.0                  Park   
193         Etobicoke             1.0                  Park   
194         Etobicoke             1.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
0                Bus Stop     Food & Drink Shop                    Drugstore   
37                 Market         Women's Store         Fast Food Restaurant   
59            Coffee Shop     Convenience Store          Dumpling Restaurant   
69            Snack Place               Airport  Eastern European Restaurant   
70            Snack Place               Airport  Eastern European Restaurant   
115     Convenience Store         Women's Store          Dumpling Restaurant   
119                  Bank     Convenience Store          Dumpling Restaurant   
182            Playground                 Trail                    Drugstore   
192                 River    Falafel Restaurant                  Event Space   
193                 River    Falafel Restaurant                  Event Space   
194                 River    Falafel Restaurant                  Event Space   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0          Discount Store               Dog Run      Doner Restaurant   
37           Dessert Shop           Event Space         Grocery Store   
59                  Diner        Discount Store               Dog Run   
69         Discount Store               Dog Run      Doner Restaurant   
70         Discount Store               Dog Run      Doner Restaurant   
115                 Diner        Discount Store               Dog Run   
119        Discount Store               Dog Run      Doner Restaurant   
182    Dim Sum Restaurant                 Diner        Discount Store   
192  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
193  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
194  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   

           8th Most Common Venue 9th Most Common Venue  \
0                     Donut Shop   Dumpling Restaurant   
37          Ethiopian Restaurant   Empanada Restaurant   
59              Doner Restaurant            Donut Shop   
69                    Donut Shop             Drugstore   
70                    Donut Shop             Drugstore   
115             Doner Restaurant            Donut Shop   
119                   Donut Shop             Drugstore   
182                      Dog Run      Doner Restaurant   
192  Eastern European Restaurant          Dessert Shop   
193  Eastern European Restaurant          Dessert Shop   
194  Eastern European Restaurant          Dessert Shop   

          10th Most Common Venue  
0             Dim Sum Restaurant  
37             Electronics Store  
59                     Drugstore  
69           Dumpling Restaurant  
70           Dumpling Restaurant  
115                    Drugstore  
119  Eastern European Restaurant  
182                   Donut Shop  
192                    Drugstore  
193                    Drugstore  
194                    Drugstore

Cluster 3

In [149]:
parkwoods_merged.loc[parkwoods_merged['Cluster Labels'] == 2, parkwoods_merged.columns[[1] + list(range(5, parkwoods_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
95  North York             2.0          Home Service          Dessert Shop   
96  North York             2.0          Home Service          Dessert Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
95                 Diner        Discount Store               Dog Run   
96                 Diner        Discount Store               Dog Run   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
95      Doner Restaurant            Donut Shop             Drugstore   
96      Doner Restaurant            Donut Shop             Drugstore   

   9th Most Common Venue 10th Most Common Venue  
95   Dumpling Restaurant          Women's Store  
96   Dumpling Restaurant          Women's Store

Cluster 4

In [150]:
parkwoods_merged.loc[parkwoods_merged['Cluster Labels'] == 3, parkwoods_merged.columns[[1] + list(range(5, parkwoods_merged.shape[1]))]]

Borough  Cluster Labels          1st Most Common Venue  \
105  North York             3.0  Paper / Office Supplies Store   
106  North York             3.0  Paper / Office Supplies Store   
197   Etobicoke             3.0                      Locksmith   
198   Etobicoke             3.0                      Locksmith   
199   Etobicoke             3.0                      Locksmith   
200   Etobicoke             3.0                      Locksmith   
201   Etobicoke             3.0                      Locksmith   
202   Etobicoke             3.0                      Locksmith   
203   Etobicoke             3.0                      Locksmith   
204   Etobicoke             3.0                      Locksmith   

    2nd Most Common Venue        3rd Most Common Venue 4th Most Common Venue  \
105        Baseball Field                Women's Store   Dumpling Restaurant   
106        Baseball Field                Women's Store   Dumpling Restaurant   
197        Baseball Field  Eastern European Restaurant               Dog Run   
198        Baseball Field  Eastern European Restaurant               Dog Run   
199        Baseball Field  Eastern European Restaurant               Dog Run   
200        Baseball Field  Eastern European Restaurant               Dog Run   
201        Baseball Field  Eastern European Restaurant               Dog Run   
202        Baseball Field  Eastern European Restaurant               Dog Run   
203        Baseball Field  Eastern European Restaurant               Dog Run   
204        Baseball Field  Eastern European Restaurant               Dog Run   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
105        Discount Store               Dog Run      Doner Restaurant   
106        Discount Store               Dog Run      Doner Restaurant   
197      Doner Restaurant            Donut Shop             Drugstore   
198      Doner Restaurant            Donut Shop             Drugstore   
199      Doner Restaurant            Donut Shop             Drugstore   
200      Doner Restaurant            Donut Shop             Drugstore   
201      Doner Restaurant            Donut Shop             Drugstore   
202      Doner Restaurant            Donut Shop             Drugstore   
203      Doner Restaurant            Donut Shop             Drugstore   
204      Doner Restaurant            Donut Shop             Drugstore   

    8th Most Common Venue 9th Most Common Venue       10th Most Common Venue  
105            Donut Shop             Drugstore  Eastern European Restaurant  
106            Donut Shop             Drugstore  Eastern European Restaurant  
197   Dumpling Restaurant     Electronics Store                        Diner  
198   Dumpling Restaurant     Electronics Store                        Diner  
199   Dumpling Restaurant     Electronics Store                        Diner  
200   Dumpling Restaurant     Electronics Store                        Diner  
201   Dumpling Restaurant     Electronics Store                        Diner  
202   Dumpling Restaurant     Electronics Store                        Diner  
203   Dumpling Restaurant     Electronics Store                        Diner  
204   Dumpling Restaurant     Electronics Store                        Diner

Cluster 5

In [151]:
parkwoods_merged.loc[parkwoods_merged['Cluster Labels'] == 4, parkwoods_merged.columns[[1] + list(range(5, parkwoods_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
53       Scarborough             4.0                   Spa   
149  Central Toronto             4.0            Playground   
150  Central Toronto             4.0            Playground   
154      Scarborough             4.0                   Gym   
155      Scarborough             4.0                   Gym   
156      Scarborough             4.0                   Gym   
157      Scarborough             4.0                   Gym   

    2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
53             Playground     Convenience Store  Eastern European Restaurant   
149         Women's Store   Dumpling Restaurant                        Diner   
150         Women's Store   Dumpling Restaurant                        Diner   
154                  Park           Coffee Shop                   Playground   
155                  Park           Coffee Shop                   Playground   
156                  Park           Coffee Shop                   Playground   
157                  Park           Coffee Shop                   Playground   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
53         Discount Store               Dog Run      Doner Restaurant   
149        Discount Store               Dog Run      Doner Restaurant   
150        Discount Store               Dog Run      Doner Restaurant   
154             Drugstore                 Diner        Discount Store   
155             Drugstore                 Diner        Discount Store   
156             Drugstore                 Diner        Discount Store   
157             Drugstore                 Diner        Discount Store   

    8th Most Common Venue 9th Most Common Venue       10th Most Common Venue  
53             Donut Shop             Drugstore          Dumpling Restaurant  
149            Donut Shop             Drugstore  Eastern European Restaurant  
150            Donut Shop             Drugstore  Eastern European Restaurant  
154               Dog Run      Doner Restaurant                   Donut Shop  
155               Dog Run      Doner Restaurant                   Donut Shop  
156               Dog Run      Doner Restaurant                   Donut Shop  
157               Dog Run      Doner Restaurant                   Donut Shop